# PPO in Stable Baselines

In single-agent PPO, `MlpPolicy` was used in `PPO1` as follows:

```
model = PPO1(MlpPolicy, env, timesteps_per_actorbatch=4096, clip_param=0.2, entcoeff=0.0, optim_epochs=10,
                 optim_stepsize=3e-4, optim_batchsize=64, gamma=0.99, lam=0.95, schedule='linear', verbose=2)

```

`MlpPolicy` is found in `stable_baselines/common/policies.py`, inheriting `FeedForwardPolicy`, which inherits from `ActorCriticPolicy`.

In `FeedForwardPolicy`'s `__init__`, there contains the following:
```
if net_arch is None:
    if layers is None:
        layers = [64, 64]
    net_arch = [dict(vf=layers, pi=layers)]

with tf.variable_scope("model", reuse=reuse):
    if feature_extraction == "cnn":
        pi_latent = vf_latent = cnn_extractor(self.processed_obs, **kwargs)
    else:
        pi_latent, vf_latent = mlp_extractor(tf.layers.flatten(self.processed_obs), net_arch, act_fun)

    self._value_fn = linear(vf_latent, 'vf', 1)

    self._proba_distribution, self._policy, self.q_value = \
        self.pdtype.proba_distribution_from_latent(pi_latent, vf_latent, init_scale=0.01)
```

Since `MlpPolicy` uses `feature_extraction="mlp"`, look into `mlp_extractor` (here)[https://github.com/hill-a/stable-baselines/blob/master/stable_baselines/common/policies.py].

`mlp_extractor` constructs a MLP that receive observations as input and outputs a latent representation for the policy and a value network. Amount and size of hidden layers and how many shared between policy and value network can be spcified using `net_arch`.

In `mlp_extractor`, it iterates through `net_arch` and creates layers, specifically using `latent = act_fun(linear(latent, ...))`. Therfore, look into `act_fun` and `linear`, which belongs in stable_baselines.common.tf_layers.

`FeedForwardPolicy`'s default for `act_fun` is `tf.tanh`. Linear contains:

```
def linear(input_tensor, scope, n_hidden, *, init_scale=1.0, init_bias=0.0):
    """
    Creates a fully connected layer for TensorFlow
    :param input_tensor: (TensorFlow Tensor) The input tensor for the fully connected layer
    :param scope: (str) The TensorFlow variable scope
    :param n_hidden: (int) The number of hidden neurons
    :param init_scale: (int) The initialization scale
    :param init_bias: (int) The initialization offset bias
    :return: (TensorFlow Tensor) fully connected layer
    """
    with tf.variable_scope(scope):
        n_input = input_tensor.get_shape()[1].value
        weight = tf.get_variable("w", [n_input, n_hidden], initializer=ortho_init(init_scale))
        bias = tf.get_variable("b", [n_hidden], initializer=tf.constant_initializer(init_bias))
        return tf.matmul(input_tensor, weight) + bias
```

Therefore, to transform this model into a Bayesian neural network, the linear layer needs to be changed into DenseVariational instead of a linear layer. We can do this by modifying `FeedForwardPolicy` (which `MlpPolicy` inherits) with a new `bnn_extractor`, then creating a `BnnPolicy` to replace `MlpPolicy`.

In [44]:
from tensorflow.keras import backend as K
from tensorflow.keras import activations, initializers
from tensorflow.keras.layers import Layer

import tensorflow as tf
import tensorflow_probability as tfp

tfd = tfp.distributions
tfp.__version__

'0.8.0'

In [45]:
def bnn_extractor(flat_observations, net_arch, act_fun):
    """
    Constructs an variational layer that receives observations as an input and outputs a latent representation for the policy and
    a value network. The ``net_arch`` parameter allows to specify the amount and size of the hidden layers and how many
    of them are shared between the policy network and the value network. It is assumed to be a list with the following
    structure:
    1. An arbitrary length (zero allowed) number of integers each specifying the number of units in a shared layer.
       If the number of ints is zero, there will be no shared layers.
    2. An optional dict, to specify the following non-shared layers for the value network and the policy network.
       It is formatted like ``dict(vf=[<value layer sizes>], pi=[<policy layer sizes>])``.
       If it is missing any of the keys (pi or vf), no non-shared layers (empty list) is assumed.
    For example to construct a network with one shared layer of size 55 followed by two non-shared layers for the value
    network of size 255 and a single non-shared layer of size 128 for the policy network, the following layers_spec
    would be used: ``[55, dict(vf=[255, 255], pi=[128])]``. A simple shared network topology with two layers of size 128
    would be specified as [128, 128].
    :param flat_observations: (tf.Tensor) The observations to base policy and value function on.
    :param net_arch: ([int or dict]) The specification of the policy and value networks.
        See above for details on its formatting.
    :param act_fun: (tf function) The activation function to use for the networks.
    :return: (tf.Tensor, tf.Tensor) latent_policy, latent_value of the specified network.
        If all layers are shared, then ``latent_policy == latent_value``
    """
    latent = flat_observations
    policy_only_layers = []  # Layer sizes of the network that only belongs to the policy network
    value_only_layers = []  # Layer sizes of the network that only belongs to the value network
    kernel_divergence_fn=lambda q, p, _: tfp.distributions.kl_divergence(q, p)

    # Iterate through the shared layers and build the shared parts of the network
    for idx, layer in enumerate(net_arch):
        if isinstance(layer, int):  # Check that this is a shared layer
            layer_size = layer
#             latent = act_fun(linear(latent, "shared_fc{}".format(idx), layer_size, init_scale=np.sqrt(2)))
            latent = act_fun(tfp.layers.DenseFlipout(layer_size, name="shared_fc{}".format(idx), activation='relu', kernel_divergence_fn=kernel_divergence_fn)(latent))
        else:
            assert isinstance(layer, dict), "Error: the net_arch list can only contain ints and dicts"
            if 'pi' in layer:
                assert isinstance(layer['pi'], list), "Error: net_arch[-1]['pi'] must contain a list of integers."
                policy_only_layers = layer['pi']

            if 'vf' in layer:
                assert isinstance(layer['vf'], list), "Error: net_arch[-1]['vf'] must contain a list of integers."
                value_only_layers = layer['vf']
            break  # From here on the network splits up in policy and value network

    # Build the non-shared part of the network
    latent_policy = latent
    latent_value = latent
    for idx, (pi_layer_size, vf_layer_size) in enumerate(zip_longest(policy_only_layers, value_only_layers)):
        if pi_layer_size is not None:
            assert isinstance(pi_layer_size, int), "Error: net_arch[-1]['pi'] must only contain integers."
#             latent_policy = act_fun(linear(latent_policy, "pi_fc{}".format(idx), pi_layer_size, init_scale=np.sqrt(2)))
            latent_policy = act_fun(tfp.layers.DenseFlipout(pi_layer_size, name="pi_fc{}".format(idx), activation='relu', kernel_divergence_fn=kernel_divergence_fn)(latent))

        if vf_layer_size is not None:
            assert isinstance(vf_layer_size, int), "Error: net_arch[-1]['vf'] must only contain integers."
#             latent_value = act_fun(linear(latent_value, "vf_fc{}".format(idx), vf_layer_size, init_scale=np.sqrt(2)))
            latent_value = act_fun(tfp.layers.DenseFlipout(vf_layer_size, name="vf_fc{}".format(idx), activation='relu', kernel_divergence_fn=kernel_divergence_fn)(latent))

    return latent_policy, latent_value

In [46]:
from stable_baselines.common.policies import ActorCriticPolicy, nature_cnn

class FeedForwardPolicy(ActorCriticPolicy):
    """
    Policy object that implements actor critic, using a feed forward neural network.
    :param sess: (TensorFlow session) The current TensorFlow session
    :param ob_space: (Gym Space) The observation space of the environment
    :param ac_space: (Gym Space) The action space of the environment
    :param n_env: (int) The number of environments to run
    :param n_steps: (int) The number of steps to run for each environment
    :param n_batch: (int) The number of batch to run (n_envs * n_steps)
    :param reuse: (bool) If the policy is reusable or not
    :param layers: ([int]) (deprecated, use net_arch instead) The size of the Neural network for the policy
        (if None, default to [64, 64])
    :param net_arch: (list) Specification of the actor-critic policy network architecture (see mlp_extractor
        documentation for details).
    :param act_fun: (tf.func) the activation function to use in the neural network.
    :param cnn_extractor: (function (TensorFlow Tensor, ``**kwargs``): (TensorFlow Tensor)) the CNN feature extraction
    :param feature_extraction: (str) The feature extraction type ("cnn" or "mlp")
    :param kwargs: (dict) Extra keyword arguments for the nature CNN feature extraction
    """

    def __init__(self, sess, ob_space, ac_space, n_env, n_steps, n_batch, reuse=False, layers=None, net_arch=None,
                 act_fun=tf.tanh, cnn_extractor=nature_cnn, feature_extraction="cnn", **kwargs):
        super(FeedForwardPolicy, self).__init__(sess, ob_space, ac_space, n_env, n_steps, n_batch, reuse=reuse,
                                                scale=(feature_extraction == "cnn"))

        self._kwargs_check(feature_extraction, kwargs)

        if layers is not None:
            warnings.warn("Usage of the `layers` parameter is deprecated! Use net_arch instead "
                          "(it has a different semantics though).", DeprecationWarning)
            if net_arch is not None:
                warnings.warn("The new `net_arch` parameter overrides the deprecated `layers` parameter!",
                              DeprecationWarning)

        if net_arch is None:
            if layers is None:
                layers = [64, 64]
            net_arch = [dict(vf=layers, pi=layers)]

        with tf.variable_scope("model", reuse=reuse):
            if feature_extractifon == "cnn":
                pi_latent = vf_latent = cnn_extractor(self.processed_obs, **kwargs)
            elif feature_extraction == "bnn":
                pi_latent, vf_latent = bnn_extractor(tf.layers.flatten(self.processed_obs), net_arch, act_fun)
            else:
                pi_latent, vf_latent = mlp_extractor(tf.layers.flatten(self.processed_obs), net_arch, act_fun)

            self._value_fn = linear(vf_latent, 'vf', 1)

            self._proba_distribution, self._policy, self.q_value = \
                self.pdtype.proba_distribution_from_latent(pi_latent, vf_latent, init_scale=0.01)

        self._setup_init()

    def step(self, obs, state=None, mask=None, deterministic=False):
        if deterministic:
            action, value, neglogp = self.sess.run([self.deterministic_action, self.value_flat, self.neglogp],
                                                   {self.obs_ph: obs})
        else:
            action, value, neglogp = self.sess.run([self.action, self.value_flat, self.neglogp],
                                                   {self.obs_ph: obs})
        return action, value, self.initial_state, neglogp

    def proba_step(self, obs, state=None, mask=None):
        return self.sess.run(self.policy_proba, {self.obs_ph: obs})

    def value(self, obs, state=None, mask=None):
        return self.sess.run(self.value_flat, {self.obs_ph: obs})

In [47]:
import warnings
from itertools import zip_longest
from abc import ABC, abstractmethod

import numpy as np
import tensorflow as tf
from gym.spaces import Discrete

from stable_baselines.common.tf_util import batch_to_seq, seq_to_batch
from stable_baselines.common.tf_layers import conv, linear, conv_to_fc, lstm
from stable_baselines.common.distributions import make_proba_dist_type, CategoricalProbabilityDistribution, \
    MultiCategoricalProbabilityDistribution, DiagGaussianProbabilityDistribution, BernoulliProbabilityDistribution
from stable_baselines.common.input import observation_input
from stable_baselines.common.policies import nature_cnn

In [48]:
class BnnPolicy(FeedForwardPolicy):
    """
    Policy object that implements actor critic, using a Bayesian neural net (2 layers of 64)
    :param sess: (TensorFlow session) The current TensorFlow session
    :param ob_space: (Gym Space) The observation space of the environment
    :param ac_space: (Gym Space) The action space of the environment
    :param n_env: (int) The number of environments to run
    :param n_steps: (int) The number of steps to run for each environment
    :param n_batch: (int) The number of batch to run (n_envs * n_steps)
    :param reuse: (bool) If the policy is reusable or not
    :param _kwargs: (dict) Extra keyword arguments for the nature CNN feature extraction
    """

    def __init__(self, sess, ob_space, ac_space, n_env, n_steps, n_batch, reuse=False, **_kwargs):
        super(BnnPolicy, self).__init__(sess, ob_space, ac_space, n_env, n_steps, n_batch, reuse,
                                        feature_extraction="bnn", **_kwargs)

# Single-Agent PPO with BNN

In [49]:
#!/usr/bin/env python3

# Train single CPU PPO1 on slimevolley.
# Should solve it (beat existing AI on average over 1000 trials) in 3 hours on single CPU, within 3M steps.

import os
import gym
import slimevolleygym
from slimevolleygym import SurvivalRewardEnv

from stable_baselines.ppo1 import PPO1
from stable_baselines.common.policies import MlpPolicy
from stable_baselines import logger
from stable_baselines.common.callbacks import EvalCallback

NUM_TIMESTEPS = int(5e6)
SEED = 721
EVAL_FREQ = 250000
EVAL_EPISODES = 10  # was 1000
LOGDIR = "bnn_ppo1" # moved to zoo afterwards.

logger.configure(folder=LOGDIR)

env = gym.make("SlimeVolley-v0")
env.seed(SEED)

Logging to bnn_ppo1


[721]

In [50]:
# take mujoco hyperparams (but doubled timesteps_per_actorbatch to cover more steps.)
model = PPO1(BnnPolicy, env, timesteps_per_actorbatch=4096, clip_param=0.2, entcoeff=0.0, optim_epochs=10,
                 optim_stepsize=3e-4, optim_batchsize=64, gamma=0.99, lam=0.95, schedule='linear', verbose=2)

eval_callback = EvalCallback(env, best_model_save_path=LOGDIR, log_path=LOGDIR, eval_freq=EVAL_FREQ, n_eval_episodes=EVAL_EPISODES)

model.learn(total_timesteps=NUM_TIMESTEPS, callback=eval_callback)

model.save(os.path.join(LOGDIR, "final_model")) # probably never get to this point.

env.close()

********** Iteration 0 ************


C:\Users\notes\Anaconda3\envs\slime-rl\lib\site-packages\stable_baselines\common\callbacks.py:287: UserWarning: Training and eval env are not of the same type<SlimeVolleyEnv<SlimeVolley-v0>> != <stable_baselines.common.vec_env.dummy_vec_env.DummyVecEnv object at 0x0000015502988988>
  "{} != {}".format(self.training_env, self.eval_env))


Optimizing...
     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
     7.84e-05 |       0.00000 |       0.04411 |      1.73e-05 |       2.07942
     -0.00062 |       0.00000 |       0.03292 |       0.00029 |       2.07914
     -0.00160 |       0.00000 |       0.02951 |       0.00108 |       2.07834
     -0.00268 |       0.00000 |       0.02699 |       0.00231 |       2.07711
     -0.00385 |       0.00000 |       0.02678 |       0.00383 |       2.07558
     -0.00404 |       0.00000 |       0.02534 |       0.00593 |       2.07349
     -0.00434 |       0.00000 |       0.02458 |       0.00717 |       2.07226
     -0.00456 |       0.00000 |       0.02396 |       0.00804 |       2.07140
     -0.00506 |       0.00000 |       0.02358 |       0.00846 |       2.07099
     -0.00584 |       0.00000 |       0.02300 |       0.00945 |       2.07000
Evaluating losses...
     -0.00610 |       0.00000 |       0.02276 |       0.01018 |       2.06928
-----------------------------

********** Iteration 11 ************
Optimizing...
     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
    -5.77e-05 |       0.00000 |       0.03078 |       0.00104 |       1.99237
     -0.00254 |       0.00000 |       0.02879 |       0.00186 |       1.98336
     -0.00310 |       0.00000 |       0.02836 |       0.00368 |       1.97321
     -0.00386 |       0.00000 |       0.02837 |       0.00452 |       1.96979
     -0.00529 |       0.00000 |       0.02705 |       0.00472 |       1.97222
     -0.00484 |       0.00000 |       0.02707 |       0.00474 |       1.96891
     -0.00565 |       0.00000 |       0.02647 |       0.00553 |       1.96812
     -0.00596 |       0.00000 |       0.02634 |       0.00537 |       1.96939
     -0.00653 |       0.00000 |       0.02597 |       0.00599 |       1.97178
     -0.00703 |       0.00000 |       0.02573 |       0.00636 |       1.97357
Evaluating losses...
     -0.00783 |       0.00000 |       0.02531 |       0.00617 |       

     -0.00910 |       0.00000 |       0.01785 |       0.00613 |       1.91403
     -0.00937 |       0.00000 |       0.01788 |       0.00595 |       1.91431
Evaluating losses...
     -0.00894 |       0.00000 |       0.01790 |       0.00573 |       1.91716
----------------------------------
| EpLenMean       | 636          |
| EpRewMean       | -4.8         |
| EpThisIter      | 6            |
| EpisodesSoFar   | 110          |
| TimeElapsed     | 78.1         |
| TimestepsSoFar  | 69632        |
| ev_tdlam_before | 0.809        |
| loss_ent        | 1.9171613    |
| loss_kl         | 0.0057316576 |
| loss_pol_entpen | 0.0          |
| loss_pol_surr   | -0.008941463 |
| loss_vf_loss    | 0.017901668  |
----------------------------------
********** Iteration 17 ************
Optimizing...
     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
     -0.00057 |       0.00000 |       0.01882 |       0.00151 |       1.91192
     -0.00119 |       0.00000 |       0.01809 | 

...

      0.00408 |       0.00000 |       0.00016 |       0.00079 |       0.67003
      0.00392 |       0.00000 |       0.00016 |       0.00079 |       0.67020
      0.00391 |       0.00000 |       0.00016 |       0.00077 |       0.67070
Evaluating losses...
      0.00427 |       0.00000 |       0.00014 |       0.00077 |       0.67054
-----------------------------------
| EpLenMean       | 3.01e+03      |
| EpRewMean       | -0.24         |
| EpThisIter      | 1             |
| EpisodesSoFar   | 2655          |
| TimeElapsed     | 5.64e+03      |
| TimestepsSoFar  | 4890624       |
| ev_tdlam_before | -0.538        |
| loss_ent        | 0.6705402     |
| loss_kl         | 0.0007684392  |
| loss_pol_entpen | 0.0           |
| loss_pol_surr   | 0.004265221   |
| loss_vf_loss    | 0.00014295861 |
-----------------------------------
********** Iteration 1194 ************
Optimizing...
     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
      0.00327 |       0.00000 | 

********** Iteration 1199 ************
Optimizing...
     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
      0.00194 |       0.00000 |       0.00187 |       0.00072 |       0.61599
      0.00191 |       0.00000 |       0.00188 |       0.00076 |       0.61616
      0.00183 |       0.00000 |       0.00186 |       0.00074 |       0.61581
      0.00147 |       0.00000 |       0.00194 |       0.00074 |       0.61563
      0.00180 |       0.00000 |       0.00181 |       0.00078 |       0.61633
      0.00170 |       0.00000 |       0.00186 |       0.00074 |       0.61627
      0.00169 |       0.00000 |       0.00182 |       0.00072 |       0.61623
      0.00185 |       0.00000 |       0.00177 |       0.00075 |       0.61573
      0.00162 |       0.00000 |       0.00183 |       0.00073 |       0.61629
      0.00186 |       0.00000 |       0.00180 |       0.00072 |       0.61569
Evaluating losses...
      0.00203 |       0.00000 |       0.00172 |       0.00075 |     

      0.00171 |       0.00000 |       0.00422 |       0.00068 |       0.58428
      0.00221 |       0.00000 |       0.00414 |       0.00069 |       0.58423
      0.00177 |       0.00000 |       0.00405 |       0.00070 |       0.58394
Evaluating losses...
      0.00160 |       0.00000 |       0.00407 |       0.00071 |       0.58439
----------------------------------
| EpLenMean       | 3.01e+03     |
| EpRewMean       | -0.18        |
| EpThisIter      | 1            |
| EpisodesSoFar   | 2670         |
| TimeElapsed     | 5.69e+03     |
| TimestepsSoFar  | 4935680      |
| ev_tdlam_before | 0.321        |
| loss_ent        | 0.5843869    |
| loss_kl         | 0.0007061221 |
| loss_pol_entpen | 0.0          |
| loss_pol_surr   | 0.0016013669 |
| loss_vf_loss    | 0.0040657544 |
----------------------------------
********** Iteration 1205 ************
Optimizing...
     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
      0.00218 |       0.00000 |       0.00215 

********** Iteration 1210 ************
Optimizing...
     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
      0.00264 |       0.00000 |       0.00203 |       0.00068 |       0.57522
      0.00277 |       0.00000 |       0.00198 |       0.00063 |       0.57532
      0.00254 |       0.00000 |       0.00198 |       0.00068 |       0.57504
      0.00325 |       0.00000 |       0.00198 |       0.00066 |       0.57526
      0.00279 |       0.00000 |       0.00199 |       0.00066 |       0.57538
      0.00368 |       0.00000 |       0.00194 |       0.00069 |       0.57542
      0.00287 |       0.00000 |       0.00195 |       0.00064 |       0.57553
      0.00252 |       0.00000 |       0.00194 |       0.00066 |       0.57516
      0.00330 |       0.00000 |       0.00190 |       0.00068 |       0.57519
      0.00261 |       0.00000 |       0.00193 |       0.00066 |       0.57526
Evaluating losses...
      0.00259 |       0.00000 |       0.00194 |       0.00067 |     

      0.00264 |       0.00000 |       0.00340 |       0.00076 |       0.65949
      0.00300 |       0.00000 |       0.00334 |       0.00078 |       0.65951
      0.00270 |       0.00000 |       0.00341 |       0.00076 |       0.65923
Evaluating losses...
      0.00327 |       0.00000 |       0.00336 |       0.00077 |       0.65876
----------------------------------
| EpLenMean       | 3.01e+03     |
| EpRewMean       | -0.19        |
| EpThisIter      | 1            |
| EpisodesSoFar   | 2685         |
| TimeElapsed     | 5.74e+03     |
| TimestepsSoFar  | 4980736      |
| ev_tdlam_before | 0.351        |
| loss_ent        | 0.6587631    |
| loss_kl         | 0.0007678833 |
| loss_pol_entpen | 0.0          |
| loss_pol_surr   | 0.0032675634 |
| loss_vf_loss    | 0.0033641139 |
----------------------------------
********** Iteration 1216 ************
Optimizing...
     pol_surr |    pol_entpen |       vf_loss |            kl |           ent
      0.00342 |       0.00000 |       0.00048 

In [51]:
obs = env.reset()
done = False
total_reward = 0

while not done:
    action, _states = model.predict(obs)
    obs, reward, done, info = env.step(action)
    total_reward += reward
    env.render()
env.close()
print("score:", total_reward)

score: -1


In [53]:
import base64
import IPython

def embed_mp4(filename):
    """Embeds an mp4 file in the notebook."""
    video = open(filename,'rb').read()
    b64 = base64.b64encode(video)
    tag = '''
    <video width="640" height="480" controls>
    <source src="data:video/mp4;base64,{0}" type="video/mp4">
    Your browser does not support the video tag.
    </video>'''.format(b64.decode())

    return IPython.display.HTML(tag)

In [54]:
import imageio

num_episodes = 5
video_filename = 'bnn-ppo.mp4'

with imageio.get_writer(video_filename, fps=60) as video:
    for _ in range(num_episodes):
        obs = env.reset()
        done = False
        total_reward = 0
        video.append_data(env.render('rgb_array'))
        
        while not done:
            action, _steps = model.predict(obs)
            obs, reward, done, info = env.step(action)
            total_reward += reward
            video.append_data(env.render('rgb_array'))
        
        print("score:", total_reward)

embed_mp4(video_filename)

score: -1
score: 0
score: 0
score: 0
score: -1
